In [1]:
# 1) load packages env py_dl
#racheli
import os
from keras.optimizers import RMSprop
import numpy as np
import pandas as pd 
import random
import matplotlib.pyplot as plt
%matplotlib inline
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten, Conv1D, MaxPooling1D, regularization
from keras.layers import Embedding, Reshape, Activation
from keras.utils import np_utils
from keras.utils.data_utils import get_file
from keras.preprocessing.text import Tokenizer
from keras.utils.vis_utils import model_to_dot 
from keras.preprocessing.sequence import skipgrams
from keras.preprocessing import sequence
from keras.layers import SimpleRNN
from keras import initializers
import matplotlib.pyplot as plt
from IPython.display import SVG
%matplotlib inline
os.environ['OMP_NUM_THREADS'] = '50'

2023-07-31 17:43:36.944454: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
# 2) constants and hyperparameters
L_RBNS = 20 # length of each sequence in RBNS data
O = int(1e7) # for initializing big arrays, helps reduce runtime
LIMIT_FILE_N_SEQ_READ = int(1e6) # limit the amount of seq we read from file, helps reduce runtime
ONE_HOT_DICT = {b'A': np.array([0,0,0,1], dtype=np.float16),
                b'C': np.array([0.,0.,1,0], dtype=np.float16),
                b'G': np.array([0,1,0,0], dtype=np.float16),
                b'T': np.array([1,0,0,0], dtype=np.float16),
                b'U': np.array([1,0,0,0], dtype=np.float16),
                b'N': np.array([0.25,0.25,0.25,0.25])
                }

ONE_HOT_DICT2 = {'A':[0,0,0,1],
                'C': [0,0,1,0],
                'G':[0,1,0,0],
                'T': [1,0,0,0],
                'U': [1,0,0,0],
                'N': [0.25,0.25,0.25,0.25]
                }

L_RBNS = 20 # length of each sequence in RBNS data
FILES_40 = ["RBP9" , "RBP11", "RBP15", "RBP31"] # files  with sequences len 40 and not 20

In [3]:
# 3) read files 
# list of files in RBNS_training
directory = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RBNS_training'
RBNS_training_files = []
for filename in os.listdir(directory): # Iterate over all files in the directory
    if os.path.isfile(os.path.join(directory, filename)):
        RBNS_training_files.append(filename)
# print(RBNS_training_files)

# filter out protein 1 files only
PROTEIN = "RBP1" ### TODO change 
filtered_list = [value for value in RBNS_training_files if value.startswith(str(PROTEIN)+'_')]
print(filtered_list)


['RBP1_1300nM.seq', 'RBP1_20nM.seq', 'RBP1_320nM.seq', 'RBP1_5nM.seq', 'RBP1_80nM.seq', 'RBP1_input.seq']


In [4]:
modified_list = [value.replace('RBP1_', '').replace('nM.seq', '') for value in filtered_list]

if 'RBP1_input.seq' in filtered_list: # get rid of input
    modified_list.remove('input.seq')
modified_list = sorted(modified_list, key=int)
# order file names according to concentration
prefixes = [item.split('_', 1)[0] for item in filtered_list]
suffixes = [item.split('_', 1)[1] for item in filtered_list]
modified_list = [PROTEIN+"_"+str(modified_list[i])+"nM.seq" for i in range(len(modified_list))]
modified_list.insert(0,str(PROTEIN)+"_input.seq")
print(modified_list)

['RBP1_input.seq', 'RBP1_5nM.seq', 'RBP1_20nM.seq', 'RBP1_80nM.seq', 'RBP1_320nM.seq', 'RBP1_1300nM.seq']


In [17]:
# # 4) BINARY classification - 
# prefixes = [item.split('_', 1)[0] for item in filtered_list]
# suffixes = [item.split('_', 1)[1] for item in filtered_list]

# # find the middle affinity files
# modified_list = [value.replace('RBP1_', '').replace('nM.seq', '') for value in filtered_list]
# if 'RBP1_input.seq' in filtered_list: # get rid of input
#     modified_list.remove('input.seq')
# modified_list = sorted(modified_list, key=int)

# # modified_list = [PROTEIN + "_" + value + "nM.seq" for value in modified_list[1:3]]  # the first 2 files
# modified_list = [PROTEIN + "_" + value + "nM.seq" for value in [modified_list[1], modified_list[-2]]]  # the first 2 files
# modified_list.append(str(PROTEIN+'_input.seq')) # 0
# modified_list

# # initalize np.arrays
# master_list = np.empty((O), dtype=f'|S{L_RBNS}') # sequences
# class_lables = np.zeros((O, len(modified_list))) # array of probolities per class
# n = 0

# ## running on protein 1 files only ############################################################
# for file_index, file in enumerate(modified_list):
#     #print(file_index)
#     file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RBNS_training/' + file
#     with open(file_path, 'r') as file:
#         lines = file.readlines()
#         # choose sequences from file randomly - limited to LIMIT_FILE_N_SEQ_READ
#         rng = np.random.default_rng(seed=123)
#         rand_indices = rng.choice(len(lines), size=LIMIT_FILE_N_SEQ_READ, replace=False)

#         # cut seq to 20 length randomly if len is longer find a random starting index and take 20 from there
#         if file in FILES_40: # file len 40
#             # choose random index to start from and select 20 chars - save shortend seq into master_list
#             start_index = random.randint(0, 20)
#             for index in rand_indices:
#                 seq = lines[index].split('\t')[0] # take only the sequence
#                 master_list[n] = seq[start_index:start_index+20] # shortened seq
#                 if file == str(PROTEIN+'_input.seq'):
#                     class_lables[n, file_index] = 0
#                 else:
#                     class_lables[n, file_index] = 1 # lables - 1 if in file otherwise stays 0
#                 n += 1
#         elif file == str(PROTEIN+'_input.seq'):
#               for index in rand_indices:
#                     seq = lines[index].split('\t')[0] # take only the sequence
#                     master_list[n] = seq # seq
#                     class_lables[n, file_index] = 0 # lables - 1 if in file otherwise stays 0
#                     n += 1
#         else: # file len 20 + isnt input.seq
#             for index in rand_indices:
#                     seq = lines[index].split('\t')[0] # take only the sequence
#                     master_list[n] = seq # seq
#                     class_lables[n, file_index] = 1 # lables - 1 if in file otherwise stays 0
#                     n += 1
# # free memory initlized that wasnt used 
# master_list = master_list[:n]
# class_lables = class_lables[:n]
# del lines

# # binary vec
# class_lables_binary = np.where(((class_lables[:, 0] == 1) | (class_lables[:, 1] == 1)) & (class_lables[:, 2] == 0), 1, 0)
# class_lables_binary

# # convert master_list seqences to one hot encoding
# one_hot = np.zeros((len(master_list),  L_RBNS, 4), dtype=np.float16)
# one_hot = np.array([ONE_HOT_DICT[bytes([nuc])] for seq in master_list for nuc in seq])
# one_hot = one_hot.reshape(len(master_list), -1, 4)

In [5]:
# 4) MULTICALSS classification - 
# initalize np.arrays
master_list = np.empty((O), dtype=f'|S{L_RBNS}') # sequences
class_lables = np.zeros((O, len(modified_list)), dtype=np.int8) # array of probolities per class
n = 0

## running on protein 1 files only ############################################################
for file_index, file in enumerate(modified_list):
    #print(file_index)
    file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RBNS_training/' + file
    with open(file_path, 'r') as file:
        lines = file.readlines()
        # choose sequences from file randomly - limited to LIMIT_FILE_N_SEQ_READ
        rng = np.random.default_rng(seed=123)
        rand_indices = rng.choice(len(lines), size=LIMIT_FILE_N_SEQ_READ, replace=False)

        # cut seq to 20 length randomly if len is longer find a random starting index and take 20 from there
        if file in FILES_40: # file len 40
            # choose random index to start from and select 20 chars - save shortend seq into master_list
            start_index = random.randint(0, 20)
            for index in rand_indices:
                seq = lines[index].split('\t')[0] # take only the sequence
                master_list[n] = seq[start_index:start_index+20] # shortened seq
                if file == str(PROTEIN+'_input.seq'):
                    class_lables[n, file_index] = 0
                else:
                    class_lables[n, file_index] = 1 # lables - 1 if in file otherwise stays 0
                n += 1
        elif file == str(PROTEIN+'_input.seq'):
              for index in rand_indices:
                    seq = lines[index].split('\t')[0] # take only the sequence
                    master_list[n] = seq # seq
                    class_lables[n, file_index] = 0 # lables - 1 if in file otherwise stays 0
                    n += 1
        else: # file len 20 + isnt input.seq
            for index in rand_indices:
                    seq = lines[index].split('\t')[0] # take only the sequence
                    master_list[n] = seq # seq
                    class_lables[n, file_index] = 1 # lables - 1 if in file otherwise stays 0
                    n += 1

# free memory initlized that wasnt used 
master_list = master_list[:n]
class_lables = class_lables[:n]
del lines

(6000000, 20, 4)

In [5]:
# 4) MULTICALSS classification - 
# initalize np.arrays
N = LIMIT_FILE_N_SEQ_READ * len(modified_list) # number of seqs
master_list = np.empty((N), dtype=f'|S{L_RBNS}') # sequences
class_lables = np.zeros((N, len(modified_list)), dtype=np.int8) # array of probolities per class
class_lables[:, 0] = 1 # set all to 1 for the first class (input.seq)
for i, file in enumerate(modified_list): # set the lables for the rest of the classes
    if file != str(PROTEIN + '_input.seq'):
        class_lables[LIMIT_FILE_N_SEQ_READ * i: LIMIT_FILE_N_SEQ_READ * (i + 1), i:] = 1
n = 0 # index for master_list
## running on protein 1 files only ############################################################
for file_index, file in enumerate(modified_list):
    #print(file_index)
    file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RBNS_training/' + file
    with open(file_path, 'r') as f:
        lines = [f.readline() for _ in range(LIMIT_FILE_N_SEQ_READ)] # read LIMIT_FILE_N_SEQ_READ lines
    # cut seq to 20 length randomly if len is longer find a random starting index and take 20 from there
    if file in FILES_40: # file len 40
        # choose random index to start from and select 20 chars - save shortend seq into master_list
        start_index = random.randint(0, 20)
        for line in lines:
            seq = line.split('\t')[0] # take only the sequence
            master_list[n] = seq[start_index : start_index + 20] # shortened seq
            n += 1
    else: # file len 20 + isnt input.seq
        for line in lines:
            seq = line.split('\t')[0] # take only the sequence
            master_list[n] = seq # seq
            n += 1
del lines

In [6]:
random.seed(123)
rand_master_list = np.empty((LIMIT_FILE_N_SEQ_READ * 2), dtype=f'|S{L_RBNS}') # sequences
rand_class_labels = np.zeros((LIMIT_FILE_N_SEQ_READ * 2, len(modified_list)), dtype=np.int8)
ABC = [b'A', b'C', b'G', b'T']
rand_master_list = np.array([b''.join([ABC[random.randint(0,3)] for _ in range(L_RBNS)]) for _ in range(LIMIT_FILE_N_SEQ_READ * 2)], dtype=f'|S{L_RBNS}')

In [7]:
class_lables = np.concatenate((class_lables, rand_class_labels))
master_list = np.concatenate((master_list, rand_master_list))

In [22]:
model_param_dict = {"kernel_size":3, "pool_size":2, "layers": [128, 128], "final_activation_function":"sigmoid"}

In [23]:
PAD_SIZE = model_param_dict["kernel_size"] - 1
one_hot = np.array([[ONE_HOT_DICT[bytes([nuc])] for nuc in (b"N" * PAD_SIZE + seq + b"N" * PAD_SIZE)] for seq in master_list])

In [29]:
# OLD() split into training and validation sets -- 80% training, 20% validation
# # TODO LATER: keep out 6~ proteins for validation of the end
# from sklearn.model_selection import train_test_split

# # Split the data into training and test sets
# one_hot_train_X, one_hot_valid_X, one_hot_train_Y, one_hot_valid_Y = train_test_split(master_list, class_lables, test_size=0.2, random_state=42)
# print(master_list.shape,class_lables.shape, one_hot.shape)
# print(one_hot_train_X.shape, one_hot_train_Y.shape, one_hot_valid_X.shape, one_hot_valid_Y.shape)

(6000000,) (6000000, 6) (6000000, 20, 4)
(4800000,) (4800000, 6) (1200000,) (1200000, 6)


In [26]:
# 5) NN per protien - input each seq (len 20) in master_list into NN 
    # output = vec of probabilities (one per each concentration)
    # compare output to bool numpy array (true lable)
    # backpropogation to model to minimize loss?
import tensorflow as tf

def accuracy_th(y_true, y_pred):
    y_true = tf.cast(y_true, tf.float32)  # Cast labels to float32
    threshold = 0.5
    y_pred_thresholded = tf.where(y_pred >= threshold, 1., 0.)  # Apply the threshold to the predicted probabilities
    accuracy = tf.reduce_mean(tf.cast(tf.equal(y_true, y_pred_thresholded), tf.float32))  # Calculate the accuracy
    return accuracy

output_size = 6 # number of classes
X = one_hot
Y = class_lables

# # first try - simple NN
# model_1=Sequential()
# model_1.add(Dense(11, activation="relu",input_shape=one_hot_train_X.shape[1:]))
# model_1.add(Flatten())
# model_1.add(Dense(output_size, activation=model_param_dict['final_activation_function'])) # softmax

# second try - CNN
model = Sequential()
model.add(Conv1D(filters=128, kernel_size=model_param_dict["kernel_size"], strides=1,
                 kernel_initializer=initializers.RandomNormal(stddev=0.01), activation='relu',
                 input_shape=X.shape[1:], use_bias=True, bias_initializer='RandomNormal'))
model.add(Conv1D(filters=128, kernel_size=model_param_dict["kernel_size"], strides=3))
# model.add(MaxPooling1D(pool_size=model_param_dict["pool_size"], strides=None, padding='valid', data_format='channels_last')) # MAYBE USE CONV KERNEL HERE INSTEAD 
model.add(Flatten())
model.add(Dropout(0.1))
# per layer
for layer_size in model_param_dict['layers']:
            print(f'the layer size is: {layer_size}')
            model.add(Dense(layer_size, activation='relu'))
            model.add(Dropout(0.1))
model.add(Dense(output_size, activation=model_param_dict['final_activation_function'])) 

from keras.optimizers import Adam, SGD, RMSprop
# Hyperparameters
EPHOCHS = 3
model.compile(optimizer=Adam(learning_rate = .003), loss="binary_crossentropy", metrics=[accuracy_th])
model.summary()

rng = np.random.default_rng(32)
shuf_inds = rng.permutation(X.shape[0])

X = X[shuf_inds][:int(1e6)]
Y = Y[shuf_inds][:int(1e6)]

# Compile the model with Optimizer, Loss Function and Metrics
run_hist_1 = model.fit(X, Y, batch_size=256, epochs=EPHOCHS, validation_split=0.5, shuffle=True, use_multiprocessing=True, workers=90)
model.save('/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/model_multiclass.h5') # save the model

the layer size is: 128
the layer size is: 128
Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_4 (Conv1D)           (None, 22, 128)           1664      
                                                                 
 conv1d_5 (Conv1D)           (None, 7, 128)            49280     
                                                                 
 flatten_2 (Flatten)         (None, 896)               0         
                                                                 
 dropout_6 (Dropout)         (None, 896)               0         
                                                                 
 dense_6 (Dense)             (None, 128)               114816    
                                                                 
 dropout_7 (Dropout)         (None, 128)               0         
                                                                 
 dense_7

24

In [40]:
X.shape

(8000000, 24, 4)

In [ ]:
# load the model
model = keras.models.load_model("/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/model_multiclass.h5")

2023-07-31 11:27:39.382810: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-07-31 11:27:39.398012: I tensorflow/core/common_runtime/process_util.cc:146] Creating new thread pool with default inter op setting: 3. Tune using inter_op_parallelism_threads for best performance.


In [ ]:
# TODO - hyperparameter tuning
# 1) number of layers -- 1, 2, 3
# 2) number of neurons per layer -- 32, 64, 128
# 3) activation function -- "relu", "sigmoid", "tanh"
# 4) optimizer -- "adam", "sgd", "rmsprop"
# 5) learning rate -- 0.001, 0.01, 0.1
# 6) batch size -- 8, 16, 32, 64, 128, 256, 512, 1024
# 7) number of epochs -- 1, 2, 4, 8
# 8) kernel size -- 3, 5, 7
# 9) pool size -- none, 2, 3, 4

In [31]:
# 6) TRYING TO RE-BUILD SHIFTS FOR PRED
# cut seg from RNAcomplete file into all shifts of len 20
INPUT_LEN = one_hot[0].shape[0]
# read txt file
file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RNAcompete_sequences.txt'
with open(file_path, 'r') as file:
    # convert seqences to one hot encoding + pad
    RNAcompete_master_list_one_hot = [[ONE_HOT_DICT2[nuc] for nuc in ((41 - len(seq.rstrip('\n'))) * 'N' + seq.rstrip('\n'))] for seq in file if len(seq) > 5]
num_seqs = len(RNAcompete_master_list_one_hot)

# SHIFTS - ut seg from RNAcomplete file into all shifts of len 20 -- create k-mers of all possible shifts 
shifts_RNAcompete_master_list = [[seq[i:i+INPUT_LEN] for i in range(0, len(seq) - INPUT_LEN + 1, 5)] for seq in RNAcompete_master_list_one_hot] # step +5 - 41,4 > 20,4
shifts_RNAcompete_master_list = np.reshape(shifts_RNAcompete_master_list, (-1, INPUT_LEN, 4))

In [37]:
# # BINARY parallelize the prediction + output ##################################################################################################################

# # predict for one datapoint is scalar => prediction.shape = (num_seqs, -1)
# # predict for one datapoint is vector N dim => prediction.shape = (num_seqs, -1, N)

# prediction = model.predict(shifts_RNAcompete_master_list, use_multiprocessing=True, workers=90)
# prediction = np.reshape(prediction, (num_seqs, -1))
# max_prediction = np.max(prediction, axis=1)
# max_prediction.shape

# write pred into file
protein="RBP1"
with open(f'/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/max_predicitions_{protein}.txt', "w") as file:
    for pred in max_prediction:
        file.write(f'{pred}\n')


37713/37713 [==============================] - 37s 973us/step


(241357,)

In [32]:
# MULTICLASS parallelize the prediction + output -  suppose predict gives N dim vector:
N = 6 # number of classes
prediction = model.predict(shifts_RNAcompete_master_list, use_multiprocessing=True, workers=90)
prediction = np.reshape(prediction, (num_seqs, -1, N))
features = np.empty((num_seqs, 2 * N))
features[:, :N] = np.max(prediction, axis=1) # shape is (num_seqs, N)
features[:, N:] = np.min(prediction, axis=1) # shape is (num_seqs, N)


# # write pred into file
# protein="RBP1"
# with open(f'/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/max_predicitions_{protein}.txt', "w") as file:
#     for pred in max_prediction:
#         file.write(f'{pred}\n')

30170/30170 [==============================] - 36s 1ms/step


In [45]:
# LinearRegression - between y_hat and y_target
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
X = np.array(features)  # Independent variable (features)


with open('/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RNCMPT_training/RBP1.txt','r') as file:
    y_target=[float(line.strip()) for line in file if line != ""] ### y

y = np.array(y_target)  # Dependent variable (target)

model = LinearRegression()
model.fit(X, y)
y_pred = model.predict(X)

from scipy.stats import pearsonr
correlation, _ = pearsonr(y, y_pred)
print(correlation)

# correlation_coefficient, p_value = stats.pearsonr(y_target, features_max)
# print("Pearson correlation coefficient:", correlation_coefficient, "p-value:", p_value)


# # Print the coefficients (slope and intercept)
# print("Coefficients:", model.coef_)     # Slope
# print("Intercept:", model.intercept_)   # Intercept
# # print("Maximum:", max(y_pred))
# # print("Minimum:", min(y_pred))

# # Visualize the linear regression line
# plt.scatter(X, y) 
# plt.plot(X, y_pred, color='red', label='Linear Regression') ## model
# plt.show()

0.27241164380909


In [48]:
X.shape

(241357, 12)

In [53]:
from sklearn.model_selection import train_test_split

with open('/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RNCMPT_training/RBP1.txt','r') as file:
    y_target=[float(line.strip()) for line in file if line != ""]

# Number of output neurons (1 for Pearson correlation)
output_neurons = 1

# Create a Sequential model
model = Sequential()

# Add a single neuron layer with 'linear' activation (no activation)
model.add(Dense(1, activation='linear', input_shape=(features.shape[1],)))


In [54]:

# Define the custom Pearson correlation coefficient loss function
def pearson_correlation(y_true, y_pred):
    y_true_mean = tf.reduce_mean(y_true)
    y_pred_mean = tf.reduce_mean(y_pred)
    covariance = tf.reduce_mean((y_true - y_true_mean) * (y_pred - y_pred_mean))
    y_true_std = tf.math.reduce_std(y_true)
    y_pred_std = tf.math.reduce_std(y_pred)
    correlation = covariance / (y_true_std * y_pred_std)
    return 1 - correlation  # Return 1 - correlation to minimize the negative correlation

# Compile the model with the custom loss function
model.compile(optimizer='adam', loss=pearson_correlation)
# Fit the model to the data
model.fit(features, y_target, batch_size=32, epochs=10, validation_split=0.2)


ValueError: `validation_split` is only supported for Tensors or NumPy arrays, found following types in the input: [<class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <class 'float'>, <

In [47]:
# Get the coefficients and the intercept
coefficients = model.coef_
intercept = model.intercept_

# Create the formula for the Linear Regression model
formula_parts = [f"{coeff:.4f}" for coeff in coefficients]
formula = f"y = {intercept:.4f} + " + " + ".join(formula_parts)

print("Linear Regression Formula:")
print(formula)

Linear Regression Formula:
y = 1.1906 + -15.2344 + 20.3540 + -9.8116 + -9.1625 + -1.7815 + 24.2165 + -4.4641 + -15.8454 + 11.6378 + -11.0284 + 2.0439 + 8.7680


In [ ]:
model

In [42]:
# reloud model + read pred + check correlation
import scipy.stats as stats
with open('/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RNCMPT_training/RBP1.txt','r') as file:
    y_target=[float(line.strip()) for line in file] ### y
       
# with open('/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/max_predicitions_RBP1.txt','r') as file:
#     y_hat=[float(line.strip('[]\n')) for line in file] ### x

correlation_coefficient, p_value = stats.pearsonr(y_target, features_max)
print("Pearson correlation coefficient:", correlation_coefficient, "p-value:", p_value)

Pearson correlation coefficient: 0.016236474757634924 p-value: 1.4974390836800376e-15


In [38]:
# # test -- one seq from input file -- should calssify as 0 - check!

# file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RBNS_training/RBP1_input.txt'
# with open(file_path, 'r') as file:
#     first_line = file.readline()
#     second_line = file.readline()

# # Extract the first element from both lines
# seq1 = first_line.split('\t')[0]
# seq2 = second_line.split('\t')[0]
# # print(seq1)

# one_hot_test_1 = np.array([ONE_HOT_DICT2[(nuc)] for nuc in seq1])
# one_hot_test_2 = np.array([ONE_HOT_DICT2[(nuc)] for nuc in seq2])
# # print(one_hot_test_1.shape)
# # print(one_hot_test_1)
# one_hot_test = np.array([one_hot_test_1, one_hot_test_2])
# # one_hot_test.shape

# # print(one_hot_test)
# # print(one_hot_test.shape)
# # model.predict(one_hot_test)

# # create prediction per seq - take max pred 1 seq
# predictions = [model.predict(one_hot_test)]
# predictions

1/1 [==============================] - 0s 115ms/step


[array([[0.6634457 ],
        [0.64907414]], dtype=float32)]

In [37]:
# # test --  one seq from input file -- should calssify as 1 - check!

# file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RBNS_training/RBP1_80nM.seq'
# with open(file_path, 'r') as file:
#     first_line = file.readline()
#     second_line = file.readline()

# # Extract the first element from both lines
# seq1 = first_line.split('\t')[0]
# seq2 = second_line.split('\t')[0]
# # print(seq1)

# one_hot_test_1 = np.array([ONE_HOT_DICT2[(nuc)] for nuc in seq1])
# one_hot_test_2 = np.array([ONE_HOT_DICT2[(nuc)] for nuc in seq2])
# print(one_hot_test_1.shape)
# # print(one_hot_test_1)
# one_hot_test = np.array([one_hot_test_1, one_hot_test_2])
# # print(one_hot_test.shape)
# # print(one_hot_test)

# # print(one_hot_test)
# # print(one_hot_test.shape)
# # model.predict(one_hot_test)

# # # create prediction per seq - take max pred 1 seq
# predictions = [model.predict(one_hot_test)]
# predictions

(20, 4)
1/1 [==============================] - 0s 78ms/step


[array([[0.67058665],
        [0.67228156]], dtype=float32)]

In [41]:
# # # cut seg from RNAcomplete file into all shifts of len 20
# # RNAcompete_master_list_one_hot = np.empty((O), dtype=f'|S{L_RBNS*2}') # sequences

# # # read txt file
# # file_path = '/data01/private/resources/RACHELI_EDEN_SHARED/DL_PROJ/RNAcompete_sequences.txt'
# # with open(file_path, 'r') as file:
# #     # convert seqences to one hot encoding
# #     RNAcompete_master_list_one_hot = [[ONE_HOT_DICT2[nuc] for nuc in seq.rstrip('\n')] for seq in file]

# # cut seg from RNAcomplete file into all shifts of len 20
# shifts_RNAcompete_master_list = np.empty((O), dtype=object) # sequences

# for n, seq_onehot in enumerate(RNAcompete_master_list_one_hot): # seq
#     line_length = len(seq_onehot)
#     if line_length > 20: # create k-mers of all possible shifts 
#         shifts = np.empty((line_length - 20), dtype=object)
#         j=0
#         if j <= 6:
#             for i in range(line_length - 20): # shift
#                 shifts[i] = np.array(seq_onehot[j:j+20])
#                 j+=3
#         shifts_RNAcompete_master_list[n] = shifts
#     else:
#         shifts_RNAcompete_master_list[n] = seq_onehot
                
# # shifts_RNAcompete_master_list[:n]

In [24]:
# logistic regresstion - maximizenp
# input: features output:
import statsmodels.api as sm


y_pred = sm.add_constant(df)

# Create a logistic regression model
logit_model = sm.Logit(y_target, y_pred)
logit_result = logit_model.fit()
print(logit_result.summary())

ValueError: endog must be in the unit interval.

cut

In [ ]:
# # cut seg from RNAcomplete file into all shifts of len 20
# shifts_RNAcompete_master_list = np.empty((O), dtype=object) # sequences


# with open(file_path, 'r') as file:
#         for n, line in enumerate(file):
#             line = line.rstrip('\n')  # Remove newline character from the end
#             line_length = len(line)
#             if line_length > 20: # create k-mers of all possible shifts 
#                 shifts = np.empty((line_length - 20 + 1), dtype=f'|S{L_RBNS}')
#                 for i in range(line_length - 20 + 1):
#                     shifts[i] = line[i:i+20]
#                     #shifts_RNAcompete_master_list[n] = line[i:i+20]
#                     # n += 1
#                 shifts_RNAcompete_master_list[n] = shifts
#             else:
#                 shifts_RNAcompete_master_list[n] = line
                
# shifts_RNAcompete_master_list[:n]

In [ ]:
# 4) model feature to find RNCMPT_train on all proteins